## Protein Hunter Chai

In [ ]:
import os
import gc
import re

import torch

from chai_ph.design import optimize_protein_design, sample_seq
from chai_ph.predict import ChaiFolder
from LigandMPNN.wrapper import LigandMPNNWrapper
from viewer.view import view

In [ ]:
folder = ChaiFolder(device="cuda:0" if torch.cuda.is_available() else "cpu")
work_dir = os.getcwd()
designer = LigandMPNNWrapper(os.path.join(work_dir, "LigandMPNN/run.py"))

/home/jupyter-yehlin/ProteinHunter


In [4]:
def is_smiles(seq):
    """Detect if sequence is SMILES string vs protein sequence"""
    smiles_chars = set("()[]=#@+-0123456789")
    return bool(set(seq.upper()) & smiles_chars)


def clean_protein_sequence(input_string: str) -> str:
    """
    Cleans a string to represent a protein sequence according to specific rules:
    1. Removes all whitespace and non-alphabetic characters.
    2. Converts all letters to uppercase.
    3. Replaces any alphabetic character that is not a standard amino acid
       one-letter code with 'X'.
    """
    # A set of the 20 standard one-letter amino acid codes for efficient lookup
    amino_acids = {
        "A",
        "C",
        "D",
        "E",
        "F",
        "G",
        "H",
        "I",
        "K",
        "L",
        "M",
        "N",
        "P",
        "Q",
        "R",
        "S",
        "T",
        "V",
        "W",
        "Y",
    }

    clean_sequence = []
    # Iterate through each character of the input string
    for char in input_string:
        # Rule 1 & 2: Only consider alphabetic characters
        if char.isalpha():
            # Rule 3: Convert to uppercase
            upper_char = char.upper()
            # Rule 4: Check if it's a valid amino acid or replace with 'X'
            if upper_char in amino_acids:
                clean_sequence.append(upper_char)
            else:
                clean_sequence.append("X")

    return "".join(clean_sequence)

In [ ]:
# @title RUN
# @markdown input options
# @markdown -----
jobname = "test"  # @param {"type":"string"}
length = 150  # @param {"type":"integer"}
percent_X = 0  # @param ["0","50","100"] {"type":"raw"}

# @markdown optional settings
seq = ""  # @param {"type":"string"}
target_seq = (
    "O=C(NCc1cocn1)c1cnn(C)c1C(=O)Nc1ccn2cc(nc2n1)c1ccccc1"  # @param {"type":"string"}
)
cyclic = False  # @param {"type":"boolean"}

# @markdown optimization options
# @markdown -----
n_trials = 4  # @param ["1","2","4","8","16"] {"type":"raw"}
n_cycles = 5  # @param ["0","1","2","3","5","10"] {"type":"raw"}
n_recycles = 3  # @param ["1","2","3"] {"type":"raw"}
n_diff_steps = 200  # @param ["50","100","200"] {"type":"raw"}
hysteresis_mode = "esm"  # @param ["templates","esm","partial_diffusion", "none"]
repredict = False  # @param {"type":"boolean"}

# @markdown mpnn options
# @markdown -----
omit_aa = ""  # @param {"type":"string"}
temperature = 0.1  # @param ["0.01","0.1","1.0"] {"type":"raw"}
scale_temp_by_plddt = False  # @param {"type":"boolean"}


# @markdown visual options
# @markdown -----
show_visual = True  # @param {"type":"boolean"}
render_freq = 1  # @param ["1","10","100"] {"type":"raw"}


###############
# Parsing opts
###############

jobname = re.sub(r"\W+", "", jobname)


def check(folder):
    return os.path.exists(folder)


if check(jobname):
    n = 0
    while check(f"{jobname}_{n}"):
        n += 1
    jobname = f"{jobname}_{n}"

binder_mode = "none"
if is_smiles(target_seq):
    binder_mode = "ligand"
else:
    target_seq = clean_protein_sequence(target_seq)
    if target_seq == "":
        target_seq = None
    else:
        binder_mode = "protein"

seq = clean_protein_sequence(seq)

omit_AA = clean_protein_sequence(omit_aa)
if omit_AA == "":
    omit_AA = None

if show_visual:
    viewer = view((600, 600), color="plddt")
else:
    viewer = None

#####################
# hysteresis_mode
#####################
opts = dict(
    use_esm=False,
    use_esm_target=binder_mode == "protein",
    pde_cutoff_intra=0.0,
    pde_cutoff_inter=0.0,
    partial_diffusion=0.0,
)
if hysteresis_mode == "templates":
    opts["pde_cutoff_intra"] = 1.5
    opts["pde_cutoff_inter"] = 3.0
elif hysteresis_mode == "esm":
    opts["use_esm"] = True
    opts["use_esm_target"] = True
elif hysteresis_mode == "partial_diffusion":
    opts["partial_diffusion"] = 0.5

# Initialize folder and designer only if they don't exist
# This allows re-running the cell without re-initializing if desired,
# but the cleanup at the end will handle memory if run multiple times.
if "folder" not in locals() or folder is None:
    folder = ChaiFolder(device="cuda:0" if torch.cuda.is_available() else "cpu")
if "designer" not in locals() or designer is None:
    designer = LigandMPNNWrapper()

X = []
for t in range(n_trials):
    if seq == "":
        trial_seq = sample_seq(length, frac_X=percent_X / 100)
    else:
        trial_seq = seq

    if viewer is not None:
        viewer.clear()

    x = optimize_protein_design(
        folder,
        designer,
        initial_seq=trial_seq,
        target_seq=target_seq,
        target_pdb=None,
        target_chain=None,
        prefix=f"chai_results/{jobname}/t{t}",
        n_steps=n_cycles,
        num_trunk_recycles=n_recycles,
        num_diffn_timesteps=n_diff_steps,
        num_diffn_samples=1,
        temperature=temperature,
        scale_temp_by_plddt=scale_temp_by_plddt,
        use_alignment=True,
        align_to="all",
        randomize_template_sequence=True,
        omit_AA=omit_AA,
        cyclic=cyclic,
        verbose=False,
        viewer=viewer,
        render_freq=render_freq,
        final_validation=repredict,
        **opts,
    )
    X.append(x)

    folder.full_cleanup()
    # Explicitly clear memory between trials
    gc.collect()
    if torch.cuda.is_available():
        torch.cuda.empty_cache()

#########################
# restore best of best
#########################
best_sco = 0
best_n = None
# Check if X is not empty before proceeding
if X:
    for n, x in enumerate(X):
        # Ensure result and ranking_score exist
        if (
            x
            and x.get("state")
            and x["state"].result
            and "ranking_score" in x["state"].result
        ):
            if x["state"].result["ranking_score"] > best_sco:
                best_sco = x["state"].result["ranking_score"]
                best_n = n
        else:
            print(
                f"Warning: Skipping trial {n} for best selection due to missing data."
            )
        folder.restore_state(X[best_n]["state"])
else:
    print("Warning: No succ essful trials completed.")
    # Handle case where X is empty

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

test_8/t3 | Step 3: score=0.317 plddt=0.7 ptm=0.729 iptm=0.214 ipae=8.90 rmsd=5.17
